<b>Spark Warmup<br><br></b>
Consider the following list of tuples, which are stored in s3://vagelis-testbucket1/test.csv (and also 
at https://vagelis-testbucket1.s3.us-west-2.amazonaws.com/test.csv)<br><br>
id,name,city,state,zipcode<br>
100,John Smith,Austin,TX,78727<br>
200,Joe Johnson,Dallas,TX,75201<br>
300,Bob Jones,Houston,TX,77028<br>
400,Andy Davis,San Antonio,TX,78227<br>
500,James Williams,Austin,TX,78727<br>
600,John Kerry,Austin,TX,78727<br>
700,Joe Ravishankar,Dallas,TX,75201<br>
800,Bob Xin,Houston,TX,77028<br>
900,Andy Cheng,San Antonio,TX,78227<br>
1000,James Brown,Austin,TX,78727<br>


a. Provide the code for reading the csv file into a Spark Dataframe


In [0]:
testdf = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/BD/test.csv")
testdf.show()

+----+---------------+-----------+-----+-------+
|  id|           name|       city|state|zipcode|
+----+---------------+-----------+-----+-------+
| 100|     John Smith|     Austin|   TX|  78727|
| 200|    Joe Johnson|     Dallas|   TX|  75201|
| 300|      Bob Jones|    Houston|   TX|  77028|
| 400|     Andy Davis|San Antonio|   TX|  78227|
| 500| James Williams|     Austin|   TX|  78727|
| 600|     John Kerry|     Austin|   TX|  78727|
| 700|Joe Ravishankar|     Dallas|   TX|  75201|
| 800|        Bob Xin|    Houston|   TX|  77028|
| 900|     Andy Cheng|San Antonio|   TX|  78227|
|1000|    James Brown|     Austin|   TX|  78727|
+----+---------------+-----------+-----+-------+



b. Find the number of lines in the csv file.

In [0]:
testdf.count()

10

c. Find the number of unique cities in the answer set.

In [0]:
testdf.select("city").distinct().count()

4

d. Find the most frequent city mentioned in the dataset

In [0]:
citydf=testdf.groupBy("city").count()
max_freq=citydf.agg({'count': 'max'}).head()[0]
filter_str = "count = {0}".format(max_freq)
citydf.filter(filter_str).select("city").show()

+------+
|  city|
+------+
|Austin|
+------+



<b>More Spark </b><br><br>
Load movies csv file available at https://www.kaggle.com/datasets/asaniczka/tmdb-moviesdataset-2023-930k-movies/.

In [0]:
from pyspark.sql.functions import mean,col,regexp_replace,lower,trim,split,avg,countDistinct,concat,explode
from pyspark.sql.types import DoubleType


moviedf = spark.read.format("csv").option("header", "true").option("multiLine","true").option("quote", "\"").option("escape", "\"").load("dbfs:/FileStore/tables/TMDB_movie_dataset_v11.csv")



id title vote_average vote_count status release_date revenue runtime adult backdrop_path budget homepage imdb_id original_language original_title overview popularity poster_path tagline genres production_companies production_countries spoken_languages 27205 Inception 8.364 34495 Released 2010-07-15 825532764 148 False /8ZTVqvKDQ8emSGUEMjsS4yHAwrp.jpg 160000000 https://www.warnerbros.com/movies/inception tt1375666 en Inception Cobb, a skilled thief who commits corporate espionage by infiltrating the subconscious of his targets is offered a chance to regain his old life as payment for a task considered to be impossible: "inception", the implantation of another person's idea into a target's subconscious. 83.952 /oYuLEt3zVCKq57qu2F8dT7NIa6f.jpg Your mind is the scene of the crime. Action, Science Fiction, Adventure Legendary Pictures, Syncopy, Warner Bros. Pictures United Kingdom, United States of America English, French, Japanese, Swahili 157336 Interstellar 8.417 32571 Released 2014-11-05 701729206 169 False /pbrkL804c8yAv3zBZR4QPEafpAR.jpg 165000000 http://www.interstellarmovie.net/ tt0816692 en Interstellar The adventures of a group of explorers who make use of a newly discovered wormhole to surpass the limitations on human space travel and conquer the vast distances involved in an interstellar voyage. 140.241 /gEU2QniE6E77NI6lCU6MxlNBvIx.jpg Mankind was born on Earth. It was never meant to die here. Adventure, Drama, Science Fiction Legendary Pictures, Syncopy, Lynda Obst Productions United Kingdom, United States of America English 155 The Dark Knight 8.512 30619 Released 2008-07-16 1004558444 152 False /nMKdUUepR0i5zn0y1T4CsSB5chy.jpg 185000000 https://www.warnerbros.com/movies/dark-knight/ tt0468569 en The Dark Knight Batman raises the stakes in his war on crime. With the help of Lt. Jim Gordon and District Attorney Harvey Dent, Batman sets out to dismantle the remaining criminal organizations that plague the streets. The partnership proves to be effective, but they soon find themselves prey to a reign of chaos unleashed by a rising criminal mastermind known to the terrified citizens of Gotham as the Joker. 130.643 /qJ2tW6WMUDux911r6m7haRef0WH.jpg Welcome to a world without rules. Drama, Action, Crime, Thriller DC Comics, Legendary Pictures, Syncopy, Isobel Griffiths, Warner Bros. Pictures United Kingdom, United States of America English, Mandarin 19995 Avatar 7.573 29815 Released 2009-12-15 2923706026 162 False /vL5LR6WdxWPjLPFRLe133jXWsh5.jpg 237000000 https://www.avatar.com/movies/avatar tt0499549 en Avatar In the 22nd century, a paraplegic Marine is dispatched to the moon Pandora on a unique mission, but becomes torn between following orders and protecting an alien civilization. 79.932 /kyeqWdyUXW608qlYkRqosgbbJyK.jpg Enter the world of Pandora. Action, Adventure, Fantasy, Science Fiction Dune Entertainment, Lightstorm Entertainment, 20th Century Fox, Ingenious Media United States of America, United Kingdom English, Spanish 24428 The Avengers 7.71 29166 Released 2012-04-25 1518815515 143 False /9BBTo63ANSmhC4e6r62OJFuK2GL.jpg 220000000 https://www.marvel.com/movies/the-avengers tt0848228 en The Avengers When an unexpected enemy emerges and threatens global safety and security, Nick Fury, director of the international peacekeeping agency known as S.H.I.E.L.D., finds himself in need of a team to pull the world back from the brink of disaster. Spanning the globe, a daring recruitment effort begins! 98.082 /RYMX2wcKCBAr24UyPD7xwmjaTn.jpg Some assembly required. Science Fiction, Action, Adventure Marvel Studios United States of America English, Hindi, Russian 293660 Deadpool 7.606 28894 Released 2016-02-09 783100000 108 False /en971MEXui9diirXlogOrPKmsEn.jpg 58000000 https://www.20thcenturystudios.com/movies/deadpool tt1431045 en Deadpool The origin story of former Special Forces operative turned mercenary Wade Wilson, who, after being subjected to a rogue experiment that leaves him with accelerated healing powers, adopts th

a. Write pyspark code to find the average vote score of all movies that contain French as a spoken language.

In [0]:
moviedf.filter(col("spoken_languages").contains("French")).select("vote_average").agg({'vote_average':'avg'}).show()

+------------------+
| avg(vote_average)|
+------------------+
|3.4633229317216374|
+------------------+



b.Write pyspark code to return the number of occurrences of each word in the movies overview. For example, if there are 2 movies with overviews “Suspense thriller” and “Suspense drama with suspense”, then the output would be:drama, 1 suspense, 3 thriller, 1 with, 1 Hints: Convert all to lowercase. Use REGEXP_REPLACE to remove special characters.Also return only top-10 words based on the number of occurrences.

In [0]:
tempdf=moviedf.withColumn("overview",lower(moviedf["overview"])).withColumn("overview", regexp_replace(col("overview"), "[^a-z0-9]+", " ")).select("overview").withColumn("overview",trim("overview"))
movierdd=tempdf.rdd.flatMap(list).filter(lambda x:x is not None).flatMap(lambda lines:lines.split(" ")).filter(lambda x:x!='').map(lambda word: (word, 1))
word_count=movierdd.reduceByKey(lambda x, y: x + y).sortBy(lambda x:x[1],ascending=False)
word_count.take(10)

[('the', 2168319),
 ('a', 1359524),
 ('and', 1183463),
 ('of', 1152484),
 ('to', 975011),
 ('in', 764380),
 ('is', 493204),
 ('his', 401053),
 ('s', 376242),
 ('with', 352821)]

c. Write pyspark code to find the 10 words with the highest score, where the 
score of a word is the average vote score of all movies that contain this word in their title. 
We only consider words that appear in at least 10 distinct titles. The output table should 
have columns word, score, and the number of titles the word appears in




In [0]:
tempdf=moviedf.withColumn("title",lower(moviedf["title"]))\
              .withColumn("title", regexp_replace(col("title"), "[^a-z0-9]+", " "))\
              .select("title","vote_average").withColumn("title",trim("title"))\
              
word_df=tempdf.select("title").withColumn("word", explode(split(col("title"), " "))).distinct()
word_count_df = word_df.groupBy("word").count().filter(col("count") >= 10)

joined_df = word_df.join(word_count_df,"word", "inner").distinct().join(tempdf,"title","inner")

result_df = joined_df.groupBy("word").agg(avg("vote_average").alias("score"),countDistinct("title").alias("no_of_titles"))
top_words_df = result_df.orderBy(col("score").desc()).limit(10)
top_words_df.show()


+----------+-----------------+------------+
|      word|            score|no_of_titles|
+----------+-----------------+------------+
|       qoc|              9.0|          26|
|       kre|             8.45|          10|
|  luthiers|8.436842105263159|          19|
| pornochic| 8.30909090909091|          44|
|    kianna|8.027272727272727|          11|
|   wondere|              8.0|          10|
|  guignols|7.937837837837837|          37|
|       wsu|7.924242424242424|          33|
|riverdance|7.907363636363636|          10|
|birkenbihl|7.814285714285715|          28|
+----------+-----------------+------------+



Now also consider a second dataset with movie reviews: https://ieee-dataport.org/openaccess/imdb-movie-reviews-dataset.

d.Load the IMDB Movie Reviews dataset into a single dataframe, which includes
movie name, year, rating, username, title, review, etc. Verify you have loaded all review 
data files by showing the total number of reviews and the number of movies in this dataset.
Hints: (1) You only need to load the review files under “2_reviews_per_movie_raw”. (2) 
There should be 1150 movies in this dataset. (3) Use “path/to/directory/*.csv” as file 
location to load all files in the same directory in Spark. (4) To correctly handle strings with 
quotes, use .option(“quote”, “\””).option(“escape”, “\””) when loading.

In [0]:
review_per_movie = spark.read.format("csv") \
  .option("header", "true") \
  .option("sep", ",") \
  .option("multiLine","true")\
  .option("quote", "\"").option("escape", "\"")\
  .load("dbfs:/FileStore/tables/review_per_movie/*.csv")\
  .select("_metadata.file_name","username" ,"rating","helpful","total","date","title","review")

review_per_movie=review_per_movie.withColumn("name",split(col("file_name"),".csv").getItem(0))
review_per_movie=review_per_movie.withColumn("name",lower(review_per_movie["name"])).withColumn("name", regexp_replace(col("name"), "_", " ")).withColumn("name",trim("name"))

movies_per_genre = spark.read.format("csv") \
  .option("header", "true") \
  .option("sep", ",") \
  .option("multiLine","true")\
  .load("dbfs:/FileStore/tables/movies_per_genre/*.csv")\

movies_per_genre=movies_per_genre.withColumn("name",lower(movies_per_genre["name"]))
movies_per_genre=movies_per_genre.withColumn("name",concat(col("name"),lit(" "),col("year")))



In [0]:
review_per_movie.count()

932464

In [0]:
review_per_movie.select("name").distinct().count()

1150

e. (6 points) Verify that you have loaded each file into the dataframe correctly by showing 
the first 10 reviews for the movie "The Caine Mutiny". Include both the review title and 
review content

In [0]:
review_per_movie.filter(review_per_movie.name.like('the caine mutiny%')).select("title","review").limit(10).display(10,truncate=False)

title review Ironically, our Navy's best remembered "mutiny"
 Historically there were two great United States Naval mutinies. In 1842 a naval sloop, the U.S.S. Somers, had a court martial for three crew members (one, Midshipman Philip Spencer, was the son of Secretary of War John Canfield Spencer), which ended with their being found guilty and hanged. To this day there is debate if Spencer (a troubled youth) was even serious about seizing the "Somers". The other occurred in 1944 at Port Chicago, California, when, a few weeks after a terrible accident that killed many men loading ammunition on a boat, their replacements refused to work under existing unsafe conditions. This led to a U.S. Supreme Court decision - against the workers, who claimed they were not under military law. But the best known mutiny in the American navy is that on the U.S.S. Caine, during the hurricane that preceded the battle of Okinawa. That this is a fictional mutiny does not seem to attract any attention. THE CAINE MUTINY was a successful novel, Broadway play ("THE CAINE MUTINY COURT MARTIAL") and a great movie. It remains the American equivalent of the mutiny on the H.M.S. Bounty. The performances of the leads, Bogart, Johnson, MacMurray (his second of three great heels), Ferrer, Tully, and E.G.Marshall are all first rate, as are the supporting cast (which includes Lee Marvin, Claude Atkins, and Jerry Paris - all of whom had quite substantial careers after this film). Only Robert Francis did not have a substantial career after his fine Ensign Keith - he died in a plane crash in 1955. There are mental images from the film (mostly connected to Bogart's Queeg) that people remember - even spoof. Every time you see some character showing nervous ticks, if he or she pulls out a pair of small metal balls and roll them in their hand, it is a salute to Bogie's originally doing it in THE CAINE MUTINY. And his magnificent moment of success: "the strawberries", and how he proved the theft with geometric precision, remains a signal that the person speaking has too many fixations. Interestingly, the film makes Queeg better (if still sick) than the play does. When cross examined by Greenwald at the court martial of Maryk and Keith, Queeg is asked about whether or not he overused his right to free transport of liquor and other items from Hawaii to the mainland from the navy. Queeg at first denies it, but when Greenwald says he can bring in (as witnesses) people connected with the sale of the items and the transport of them, Queeg suddenly remembers that he might have. This is not in the film, but it shows that Queeg was not all that clean an officer. That aside, the impact of the film is still terrific half a century after it was shot. It illustrates that personality flaws frequently causes the problems that affect all of us, and that we need more understanding of each other's problems to avoid the bigger ones. From a case of over-extended battle fatigue, the crew of a warship are driven to accept an act of mutiny against it's captain in an emergency situation. And it almost gets two officers disgraced or hanged. Bogart and MacMurray shine in this adaptation of Herman Wouk's masterpiece.
 Great novels often disappoint when brought to the screen, but superior acting performances make The Caine Mutiny a classic on its own merits. The movie takes place on a destroyer-minesweeper in the Pacific during World War II. To the consternation of the Caine's crew, a popular captain (Tom Tully) is replaced by a disturbed despot named Queeg (Humphrey Bogart), who finds himself in over his head. As the stresses of command multiply, Queeg's paranoia and cowardice soon become apparent to Lieutenant Thomas Keefer (Fred MacMurray), a writer in civilian life. Keefer continually tries to convince Executive Officer Steve Maryk (Van Johnson) that Queeg is insane, but Keefer won't help Maryk when the Exec asks Keefer to help convince higher authority that Queeg should be relieved. During a t

f. Write pyspark to count the number of movies that appear in both datasets. 
Match using title (exact match, case insensitive) and year.

In [0]:
movie_reviews = review_per_movie.join(movies_per_genre,"name", "inner")
movie_reviews.select("name").distinct().count()

943

g. Write pyspark to find the top-20 movies, with at least 100 reviews, with the 
highest average rating.

In [0]:
review_per_movie=review_per_movie.withColumn("movie_name",split(col("file_name"),".csv").getItem(0)).withColumn("movie_name", regexp_replace(col("movie_name"), "_", " "))
review_count=review_per_movie.groupBy("movie_name").count()
review_count=review_count.filter(col("count")>99)
review_count.select("movie_name").join(review_per_movie,"movie_name","inner")
review_per_movie=review_per_movie.withColumn("rating", review_per_movie["rating"].cast(DoubleType()))
movie_avg_rating=review_count.select("movie_name").join(review_per_movie,"movie_name","inner").groupBy("movie_name").agg(avg("rating").alias("avg_rating"))
movie_avg_rating.orderBy(movie_avg_rating.avg_rating.desc()).limit(20).show(truncate=False)


+---------------------------------------------------+-----------------+
|movie_name                                         |avg_rating       |
+---------------------------------------------------+-----------------+
|The Shawshank Redemption 1994                      |9.30961195667078 |
|Star Wars  Episode V   The Empire Strikes Back 1980|9.26366251198466 |
|Back to the Future 1985                            |9.262345679012345|
|The Best Years of Our Lives 1946                   |9.169565217391304|
|12 Angry Men 1957                                  |9.16131334760885 |
|Grave of the Fireflies 1988                        |9.123558484349259|
|Beauty and the Beast 1991                          |9.110803324099724|
|Terminator 2  Judgment Day 1991                    |9.094883720930232|
|Psycho 1960                                        |9.090909090909092|
|The Godfather  Part II 1974                        |9.078071182548795|
|The Godfather 1972                                 |9.073955916

h. Write pyspark to return the top-20 users with the most reviews

In [0]:
user_count=review_per_movie.groupBy("username").count()
user_count.sort("count",ascending=[False]).limit(20).show(truncate=False)

+-----------------+-----+
|username         |count|
+-----------------+-----+
|SnoopyStyle      |1119 |
|jboothmillard    |963  |
|TxMike           |818  |
|bob the moo      |750  |
|george.schmidt   |721  |
|Quinoa1984       |710  |
|classicsoncall   |678  |
|TheLittleSongbird|666  |
|anaconda-40658   |664  |
|Leofwine_draca   |663  |
|kosmasp          |655  |
|lee_eisenberg    |644  |
|lesleyharris30   |642  |
|g-bodyl          |611  |
|claudio_carvalho |609  |
|neil-476         |606  |
|gavin6942        |605  |
|grantss          |598  |
|CinemaClown      |596  |
|evanston_dad     |575  |
+-----------------+-----+

